**Register 0x1E, Register 0x1F, Register 0x20—OFSX,OFSY, OFSZ (Read/Write)**  
The OFSX, OFSY, and OFSZ registers are each eight bits and
offer user-set offset adjustments in twos complement format
    
** Register 0x2c ** 

D3,D2,D1,D0 Rate Bit sdevice bandwidth and output data rate
default 0xA, 100Hz output dara rate

|Output DataRate (Hz)| Bandwidth (Hz)| Rate Code|Hexa|
|:----|:----|:---|:-|
|3200|1600|          1111 || 
|1600|      800|           1110||   
|800|       400|           1101||  
|400|       200|           1100|0x0C| 
|200|       100|           1011|0x0B|   
|100|       50|            1010|0x0A| 
|50|        25|            1001|| 
|25|        12.5|          1000|| 
|12.5|      6.25|          0111|| 
|6.25|      3.13|          0110|| 
|3.13|      1.56|          0101|| 
|1.56|      0.78|          0100|| 
|0.78|      0.39|          0011|| 
|0.39|      0.20|          0010|| 
|0.20|      0.10|          0001|| 
|0.10|      0.05|          0000|| 

** Register 0x31 DATA_FORMAT (Read/Write)**

- **D3: FULL_RES Bit**   
When this bit is set to a value of 1, the device is in full resolution
mode, where the output resolution increases with the g range
set by the range bits to maintain a 4 mg/LSB scale factor. When
the FULL_RES bit is set to 0, the device is in 10-bit mode, and
the range bits determine the maximum g range and scale factor.  

- **D2: Justify Bit** 
A setting of 1 in the justify bit selects left-justified (MSB) mode,
and a setting of 0 selects right-justified mode with sign extension.

|D1| D0 |g Range|
|:-|:-|:-|
|0|  0|  ±2 g| 
|0|  1|  ±4 g| 
|1  |0|  ±8 g| 
|1  |1|  ±16 g| 


|OUTPUT RESOLUTION|  Each axis||
|:-|:-|:-|
|All g Ranges|  10-bit resolution|    10    Bits| 
|±2 g Range|  Full resolution|    10    Bits| 
|±4 g Range|  Full resolution|    11    Bits| 
|±8 g Range|  Full resolution|    12    Bits| 
|±16 g Range|  Full resolution|    13    Bits| 

**Register 0x2D—POWER_CTL (Read/Write)**

|D3| D2| D1| D0|
|:-|:-|:-|
|Measure|  Sleep|  Wakeup|Wakeup|


**Register 0x2E—INT_ENABLE (Read/Write)**

|D7 |D6 |D5 |D4|
|:-|:-|:-|:-|
|DATA_READY|  SINGLE_TAP|  DOUBLE_TAP|  Activity| 
|D3|  D2|  D1|  D0| 
|Inactivity|  FREE_FALL|  Watermark|  Overrun| 

Setting bits in this register to a value of 1 enables their respective  functions to generate interrupts, whereas a value of 0 prevents
the functions from generating interrupts. The DATA_READY, watermark, and overrun bits enable only the interrupt output; the functions are always enabled. It is recommended that interrupts be configured before enabling their outputs.

**Register 0x30—INT_SOURCE (Read Only)**

|D7| D6| D5| D4|
|:-|:-|:-|:-|
|DATA_READY|  SINGLE_TAP|  DOUBLE_TAP|  Activity| 
|D3|  D2|  D1|  D0| 
|Inactivity|  FREE_FALL|  Watermark|  Overrun| 

1. Set data parameters such as data rate, measurement range, data format, and offset adjustment.  
2. Configure interrupts (do not enable): thresholds and timing values, and map interrupts to pins.   
3. Configure FIFO (if in use): mode, trigger interrupt if using trigger mode, and samples bits.   
4. Enable interrupts: INT_ENABLE register.  
5. Place part into measurement mode: POWER_CTL register.  


**Register 0x38—FIFO_CTL**

|D7| D6| D5| D4| D3| D2| D1| D0|
|:-|:-|:-|:-|:-|:-|:-|:-|
|FIFO_MODE||  Trigger|  Samples|||||

|D7| D6| Mode Function|
|:-|:-|:-|
|0|  0|  Bypass  FIFO is bypassed.| 
|0|  1|  FIFO  FIFO collects up to 32 values and then stops collecting data, collecting new data only when FIFO is not full.| 
|1|  0|  Stream  FIFO holds the last 32 data values. When FIFO is full, the oldest data is overwritten with newer data.| 
|1|  1|  Trigger  When triggered by the trigger bit, FIFO holds the last data samples before the trigger event and then continues to collect data until full. New data is collected only when FIFO is not full.| 

**Trigger Bit**  
A value of 0 in the trigger bit links the trigger event of trigger mode
to INT1, and a value of 1 links the trigger event to INT2.

**Samples Bits**  
The function of these bits depends on the FIFO mode selected
(see Table 23). Entering a value of 0 in the samples bits immediately
sets the watermark status bit in the INT_SOURCE register,
regardless of which FIFO mode is selected. Undesirable operation
may occur if a value of 0 is used for the samples bits when trigger
mode is used.

|FIFO Mode |Samples Bits Function|
|:-|:-|
|Bypass|  None.| 
|FIFO  |Specifies how many FIFO entries are needed to trigger a watermark interrupt.| 
|Stream|  Specifies how many FIFO entries are needed to trigger a watermark interrupt. |
|Trigger|  Specifies how many FIFO samples are retained in the FIFO buffer before a trigger event.| 




** Register 0x32 to Register 0x37—DATAX0, DATAX1,DATAY0, DATAY1, DATAZ0, DATAZ1 (Read Only)**

These six bytes (Register 0x32 to Register 0x37) are eight bits
each and hold the output data for each axis. Register 0x32 and
Register 0x33 hold the output data for the x-axis, Register 0x34 and
Register 0x35 hold the output data for the y-axis, and Register 0x36
and Register 0x37 hold the output data for the z-axis. The output
data is twos complement, with DATAx0 as the least significant
byte and DATAx1 as the most significant byte, where x represent X,
Y, or Z. The DATA_FORMAT register (Address 0x31) controls
the format of the data. It is recommended that a multiple-byte
read of all registers be performed to prevent a change in data
between reads of sequential registers.

TODO  
check data stream

In [1]:
# -*- coding: utf-8 -*-
#!/usr/bin/python

import RPi.GPIO as GPIO
import os
import numpy as np
import smbus
import time
import signal
import pickle

from sampling_params import SAMPLING_PARAMS

class ADXL345():
    def __init__(self):
        
        self.DevAdr = 0x53
        myBus = ""
        if GPIO.RPI_INFO['P1_REVISION'] == 1:
            myBus = 0
        else:
            myBus = 1
            
        self.b = smbus.SMBus(myBus)
        
        self.b.write_byte_data(self.DevAdr, 0x2C, 0x0B) # BandwidthRate 200Hz
        self.b.write_byte_data(self.DevAdr, 0x31, 0x01) # DATA_FORMAT 10bit 4g
        self.b.write_byte_data(self.DevAdr, 0x38, 0x90) # FIFO_CTL Streaming  Streaming 16samples
        self.b.write_byte_data(self.DevAdr, 0x2D, 0x08) # POWER_CTL Enable
    
    def getOffset(self):
        data =[]
        for a in range(NO_OF_OFFSET_MEASURE):
            input = self.getData()
            data.append(input)
            time.sleep(SAMPLING_CYCLE)
        data = np.array(data)
        offset = data.mean(axis = 0)
        
        return offset
        
    def getData(self):
        int_source = self.b.read_byte_data(self.DevAdr, 0x30)
        if int_source & 0x02 == 0x02:
        
            output = []
            data = self.b.read_i2c_block_data(self.DevAdr, 0x32, 6) #block read

            for i in range(0,6,2):
                sign = data[i + 1] & 0x80
                tmp = data[i + 1] & 0x7F
                tmp = tmp << 8
                tmp = tmp | data[i]

                if sign > 0:
                    output.append(tmp - 32768)
                else:
                    output.append(tmp)

            return np.array(output)
        
        else:
            return None

def main(arg1, arg2):
    
    global Data
    
    for _ in range(16):
        data = myADXL345.getData()
        if data is not None:
            data = np.array(data - offset)
            Data.append(data)

    print "*", 

    if len(Data) > NO_OF_SAMPLES:
        
        signal.setitimer(signal.ITIMER_REAL, 0.)
        print "\nDone", time.time() - TIME_START
    
        with open('Data.pkl', 'wb') as f:
            pickle.dump(Data, f)
            
if __name__ == "__main__":
    
    NO_OF_FIFO_BUFFER = SAMPLING_PARAMS['NO_OF_FIFO_BUFFER']
    BANDWIDTH_RATE = SAMPLING_PARAMS['BANDWIDTH_RATE']
    
    SAMPLING_CYCLE = SAMPLING_PARAMS['SAMPLING_CYCLE']
    MONITOR_TIME = SAMPLING_PARAMS['MONITOR_TIME']
    
    NO_OF_SAMPLES = int(MONITOR_TIME * BANDWIDTH_RATE)
    
    print "No of samples:" , NO_OF_SAMPLES
    
    OFFSET_MEASURE_TIME = 1
    NO_OF_OFFSET_MEASURE = int(OFFSET_MEASURE_TIME * ( 1.0  / SAMPLING_CYCLE ))
    
    myADXL345 = ADXL345()

    offset = myADXL345.getOffset()

    Data =[]
    
    TIME_START = time.time()
    
    signal.signal(signal.SIGALRM, main)
    signal.setitimer(signal.ITIMER_REAL, 0.1, SAMPLING_CYCLE)

No of samples: 120000


* * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * 

 * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * *

 * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * * *

## 信号の表示

In [2]:
import pandas as pd
import pickle

from sampling_params import SAMPLING_PARAMS

from bokeh.plotting import figure
from bokeh.io import output_file, show, output_notebook
output_notebook()

with open('Data.pkl', 'rb') as f:
    Data = pickle.load(f)  
    
NO_OF_SAMPLES = len(Data)
BANDWIDTH_RATE = SAMPLING_PARAMS['BANDWIDTH_RATE']

Data = list(map(list, zip(*Data[:NO_OF_SAMPLES])))  #Swap rows and columns

t=[float(n) /  BANDWIDTH_RATE for n in range(0, NO_OF_SAMPLES)]

pp = figure(tools='xwheel_zoom,xpan',
title="",
x_axis_label='Time[sec]',
y_axis_label='Acceleration')
#pp.line(t, Data[0],legend="X", line_width=1, line_color = "blue")
#pp.line(t, Data[1],legend="Y", line_width=1, line_color = "red")
pp.line(t, Data[2],legend="Z", line_width=1, line_color = "green")
output_file("robot.html")
show(pp)

Loading BokehJS ...

## 信号処理：絶対値を取って、EMA、サブサンプリング、表示

In [3]:
import pickle

from bokeh.plotting import figure
from bokeh.io import output_file, show, output_notebook
output_notebook()

from sampling_params import SAMPLING_PARAMS

SUB_SAMPLING_RATE = SAMPLING_PARAMS['SUBSAMPLING_RATE']
FORGETING_FACTOR = SAMPLING_PARAMS['FORGETING_FACTOR']
SUBSAMPLING_RATE = SAMPLING_PARAMS['SUBSAMPLING_RATE']
BANDWIDTH_RATE = SAMPLING_PARAMS['BANDWIDTH_RATE']

with open('Data.pkl', 'rb') as f:
    Data = pickle.load(f)

NO_OF_SAMPLES = len(Data)
    
Data = list(map(list, zip(*Data[:NO_OF_SAMPLES])))  #Swap rows and columns Data[0]:X axis, Data[1] : Y axis, Data[2] : Z axis

ema = 0
Data_ema = []
Data_subsampled = []

for i in range(NO_OF_SAMPLES):
    ema = ema * (1 - FORGETING_FACTOR) + (FORGETING_FACTOR) * abs(Data[2][i])
    Data_ema.append(ema)

for i in range(0, NO_OF_SAMPLES, SUBSAMPLING_RATE ):
    Data_subsampled.append(Data_ema[i])

print "No of samples: ", len(Data_subsampled)
    
t=[float(n) /  BANDWIDTH_RATE * SUBSAMPLING_RATE for n in range(0, NO_OF_SAMPLES)]

pp = figure(tools='xwheel_zoom,xpan',
title="",
x_axis_label='Time[sec]',
y_axis_label='Acceleration')
pp.line(t, Data_subsampled,legend="Z", line_width=1, line_color = "green")
output_file("robot.html")
show(pp)

Loading BokehJS ...

No of samples:  6001


/usr/local/lib/python2.7/dist-packages/bokeh/models/sources.py:137: BokehUserWarning: ColumnDataSource's columns must be of the same length. Current lengths: ('x', 120003), ('y', 6001)
  "Current lengths: %s" % ", ".join(sorted(str((k, len(v))) for k, v in data.items())), BokehUserWarning))


## 異常検知用に、ヘッダをつけて、データを書き出し

In [4]:
import pandas as pd

df = pd.Series(['acceleration','float',''])
df = df.append(pd.Series(Data_subsampled),ignore_index=True)
df.to_csv( 'data.csv',index = False)